$$ \dot{x} = -y + ax(x^{2}+y^{2}) $$
$$ \dot{y} = x + ay(x^{2}+y^{2}) $$

### Import libraries

In [1]:
using OrdinaryDiffEq, StaticArrays, Plots, Interact

HTML{String}("<script>\n// Immediately-invoked-function-expression to avoid global variables.\n(function() {\n    var warning_div = document.getElementById(\"webio-warning-259281243175998372\");\n    var hide = function () {\n        var script = document.getElementById(\"webio-setup-2902793717193317780\");\n        var parent = script && script.parentElement;\n        var grandparent = parent && parent.parentElement;\n        if (grandparent) {\n            grandparent.style.display = \"none\";\n        }\n        warning_div.style.display = \"none\";\n    };\n    if (typeof Jupyter !== \"undefined\") {\n        console.log(\"WebIO detected Jupyter notebook environment.\");\n        // Jupyter notebook.\n        var extensions = (\n            Jupyter\n            && Jupyter.notebook.config.data\n            && Jupyter.notebook.config.data.load_extensions\n        );\n        if (extensions && extensions[\"webio-jupyter-notebook\"]) {\n            // Extension already loaded.\n            console.log(\"Jupyter WebIO nbextension detected; not loading ad-hoc.\");\n            hide();\n            return;\n        }\n    } else if (window.location.pathname.includes(\"/lab\")) {\n        // Guessing JupyterLa\n        console.log(\"Jupyter Lab detected; make sure the @webio/jupyter-lab-provider labextension is installed.\");\n        hide();\n        return;\n    }\n})();\n\n</script>\n<p\n    id=\"webio-warning-259281243175998372\"\n    class=\"output_text output_stderr\"\n    style=\"padding: 1em; font-weight: bold;\"\n>\n    Unable to load WebIO. Please make sure WebIO works for your Jupyter client.\n    For troubleshooting, please see <a href=\"https://juliagizmos.github.io/WebIO.jl/latest/providers/ijulia/\">\n    the WebIO/IJulia documentation</a>.\n    <!-- TODO: link to installation docs. -->\n</p>\n")

### uitilities 

In [7]:
function get_delay_coordinates(X,τ)
    """
    X: time series data
    τ: delay time 
    """
    x1 = [X[i] for i in range(1, step=1, length= length(X)-τ)]
    x2 = [X[i+τ] for i in range(1, step=1, length= length(X)-τ)]
    return x1,x2
    
end

get_delay_coordinates (generic function with 1 method)

### Make the set of ODES as a Julia function f

In [37]:
function ODE(u,p,t)
    
    x,y = u
    a =p
    
    ẋ = -y + a*x*(x^2 + y^2)
    ẏ = x + a*y*(x^2 + y^2)
    
    return SVector(ẋ, ẏ)
end

ODE (generic function with 1 method)

In [81]:
function ODE(u,p,t)
    
    x,y = u
    a =p

    ẋ = y
    ẏ = x-x^3

    return SVector(ẋ, ẏ)
end

ODE (generic function with 1 method)

### main function

In [98]:
function Dynamical_system(x₀, y₀,a,T,delay_cord,τ)
    
   """ 
    t : (0, T)
    delay: which delay coordinate to plot
    τ: delay time"""
    
    # initial state
    u₀ = SVector(x₀,y₀)
    # parameters
    p = [a]
    #time span
    tspan = (0.0,T)
    #define ODE problem
    prob = ODEProblem(ODE,u₀,tspan,p)
    # choose a solver
    alg = Vern9()
    # solve the ODE
    sol = solve(prob,alg=alg)
    
   

    # delay co-ordinates
    t = 0:0.01:T
    X₁,X₂ = zero(t),zero(t)
    for (i,time) in enumerate(t)
        X₁[i],X₂[i] = sol(time)
    end
    X = [X₁,X₂]
    
     #time series
    p₁ = plot(sol,vars=(0,1:2),title="trajectory")
    
     # plotting two varaibles
    p₂ = plot(X₁,X₂,title="x vs y")
    
    x₁,x₂ = get_delay_coordinates(X[delay_cord],τ)
    p₃= plot(x₁,x₂,title="delay coordinates")
    
    plot(p₁,p₂,p₃,layout=(1,3),lagend=false,size=(1000,500))
end

Dynamical_system (generic function with 1 method)

## Start simulation

### define variables

In [99]:
x₀ = widget(value=10.0,0:0.01:100, label="x₀")   
y₀ = widget(value=10.0,0:0.01:100, label="y₀")   
a = widget(value=10.0,0:0.01:100, label="a")   
T = widget(value=250,0:10:1000, label="T")
delay_cord = widget(value=1,1:1:2, label="delay_cord") 
τ = widget(value=1,1:1:100, label="tau") ;

### plot the data

In [100]:
theme(:orange)

In [101]:
# stack vertically   
vbox(hbox(x₀, y₀,a,T,delay_cord,τ),   
    map(Dynamical_system, x₀, y₀,a,T,delay_cord,τ)
    )

(div { style=Dict("display" => "flex","flex-direction" => "column") }
  (div { style=Dict("display" => "flex","flex-direction" => "row") }
    Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["x₀"], Dict{Symbol,Any}(:className => "interact ",:style => Dict{Any,Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol,Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol,Any}(:max => 10001,:min => 1,:attributes => Dict{Any,Any}(:type => "range",Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}","orient" => "horizontal"),:step => 1,:className => "slider slider is-fullwidth",:style => Dict{Any,Any}()))], Dict{Symbol,Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol,Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol,Any}(:className => "interact-flex-row-right"))], Dict{Symbol,Any}(:className => "interact-flex-row interact-widget")), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing),"index" => (Observable{Any} with 2 listeners. Value:
1001, nothing)), Set{String}(), nothing, Asset[Asset("js", "knockout", "/nethome/n.kusampudi/.julia/packages/Knockout/IP1uR/src/../assets/knockout.js"), Asset("js", "knockout_punches", "/nethome/n.kusampudi/.julia/packages/Knockout/IP1uR/src/../assets/knockout_punches.js"), Asset("js", nothing, "/nethome/n.kusampudi/.julia/packages/InteractBase/sOe2Z/src/../assets/all.js"), Asset("css", nothing, "/nethome/n.kusampudi/.julia/packages/InteractBase/sOe2Z/src/../assets/style.css"), Asset("css", nothing, "/nethome/n.kusampudi/.julia/packages/Interact/SbgIk/src/../assets/bulma_confined.min.css")], Dict{Any,Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")],"index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(sz_max:32,sz_curr:0), Set{AbstractConnection}(), Base.GenericCondition{Base.AlwaysLockedST}(Base.InvasiveLinkedList{Task}(Task (runnable) @0x0000147e4bd90010, Task (runnable) @0x0000147e4bd90010), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"0.0\",\"0.01\",\"0.02\",\"0.03\",\"0.04\",\"0.05\",\"0.06\",\"0.07\",\"0.08\",\"0.09\",\"0.1\",\"0.11\"